## Importing necessary libraries

In [25]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

import warnings
import sqlite3
from scipy.stats import ttest_ind
import scipy.stats as stats
warnings.filterwarnings('ignore')

## Loading Dataset

In [3]:
# Creating connection 
conn = sqlite3.connect('inventory.db')

# fetching vendor summary data
df = pd.read_sql_query("select * from vendor_sales_summary", conn)
df

VendorNumber                     VendorName  Brand  \
0                 2  IRA GOLDMAN AND WILLIAMS, LLP  90085   
1                 2  IRA GOLDMAN AND WILLIAMS, LLP  90609   
2                54    AAPER ALCOHOL & CHEMICAL CO    990   
3                60        ADAMBA IMPORTS INTL INC    771   
4                60        ADAMBA IMPORTS INTL INC   3401   
...             ...                            ...    ...   
10687        173357            TAMWORTH DISTILLING   2804   
10688        173357            TAMWORTH DISTILLING   3666   
10689        173357            TAMWORTH DISTILLING   3848   
10690        173357            TAMWORTH DISTILLING   3909   
10691        201359             FLAVOR ESSENCE INC  90609   

                        Description  PurchasePrice  ActualPrice  Volume  \
0      Ch Lilian 09 Ladouys St Este          23.86        36.99   750.0   
1      Flavor Essence Variety 5 Pak          17.00        24.99   162.5   
2           Ethyl Alcohol 200 Proof         105.07       134.49  3750.0   
3       Bak's Krupnik Honey Liqueur          11.44        14.99   750.0   
4                      Vesica Vodka          11.10        14.99  1750.0   
...                             ...            ...          ...     ...   
10687           Camp Robber Whiskey          32.14        44.99   750.0   
10688   Art in the Age Chicory Root          18.79        24.99   375.0   
10689            Chicory Root Vodka          23.30        30.99   750.0   
10690          White Mountain Vodka          19.37        24.99   750.0   
10691  Flavor Essence Variety 5 Pak          17.00        24.99   162.5   

       TotalPurchaseQuantity  TotalPurchaseDollars  TotalSalesQuantity  \
0                          8                190.88                18.0   
1                        320               5440.00                24.0   
2                          1                105.07                 0.0   
3                         39                446.16                47.0   
4                          6                 66.60                 0.0   
...                      ...                   ...                 ...   
10687                    210               6749.40               140.0   
10688                    520               9770.80               360.0   
10689                     28                652.40                 6.0   
10690                   1232              23863.84               982.0   
10691                      1                 17.00                59.0   

       TotalSalesDollars  TotalSalesPrice  TotalExciseTax  FreightCost  \
0                 665.82           295.92            2.00        27.08   
1                 599.76           449.82            0.52        27.08   
2                   0.00             0.00            0.00         0.48   
3                 704.53           494.67           37.01       367.52   
4                   0.00             0.00            0.00       367.52   
...                  ...              ...             ...          ...   
10687            6298.60          3194.29          110.33       202.50   
10688            8996.40          4873.05          141.19       202.50   
10689             185.94            92.97            4.71       202.50   
10690           24540.18         14469.21          773.87       202.50   
10691            1474.41          1324.47            1.24         0.09   

       GrossProfit  ProfitMargin  StockTurnover  SalesPurchaseRatio  
0           474.94     71.331591       2.250000            3.488160  
1         -4840.24   -807.029478       0.075000            0.110250  
2          -105.07          -inf       0.000000            0.000000  
3           258.37     36.672675       1.205128            1.579097  
4           -66.60          -inf       0.000000            0.000000  
...            ...           ...            ...                 ...  
10687      -450.80     -7.157146       0.666667            0.933209  
10688      -774.40     -8.607888   

## Exploratory Data Analysis

- Previously we examined the various tables in the database to identify key variables, understand their relationships and determine which one should be included in the final analysis.

- In this phase of EDA we'll analyse the resultant table to gain insights into the distribution of each column. This will help us understand data patterns, identify anomalies and ensure data quality defore proceeding with further analysis. 

In [4]:
# Summary statistics
df.describe().T

count          mean            std       min  \
VendorNumber           10692.0  1.065065e+04   18753.519148      2.00   
Brand                  10692.0  1.803923e+04   12662.187074     58.00   
PurchasePrice          10692.0  2.438530e+01     109.269375      0.36   
ActualPrice            10692.0  3.564367e+01     148.246016      0.49   
Volume                 10692.0  8.473605e+02     664.309212     50.00   
TotalPurchaseQuantity  10692.0  3.140887e+03   11095.086769      1.00   
TotalPurchaseDollars   10692.0  3.010669e+04  123067.799627      0.71   
TotalSalesQuantity     10692.0  3.077482e+03   10952.851391      0.00   
TotalSalesDollars      10692.0  4.223907e+04  167655.265984      0.00   
TotalSalesPrice        10692.0  1.879378e+04   44952.773386      0.00   
TotalExciseTax         10692.0  1.774226e+03   10975.582240      0.00   
FreightCost            10692.0  6.143376e+04   60938.458032      0.09   
GrossProfit            10692.0  1.213238e+04   46224.337964 -52002.78   
ProfitMargin           10692.0          -inf            NaN      -inf   
StockTurnover          10692.0  1.706793e+00       6.020460      0.00   
SalesPurchaseRatio     10692.0  2.504390e+00       8.459067      0.00   

                                25%           50%           75%           max  
VendorNumber            3951.000000   7153.000000   9552.000000  2.013590e+05  
Brand                   5793.500000  18761.500000  25514.250000  9.063100e+04  
PurchasePrice              6.840000     10.455000     19.482500  5.681810e+03  
ActualPrice               10.990000     15.990000     28.990000  7.499990e+03  
Volume                   750.000000    750.000000    750.000000  2.000000e+04  
TotalPurchaseQuantity     36.000000    262.000000   1975.750000  3.376600e+05  
TotalPurchaseDollars     453.457500   3655.465000  20738.245000  3.811252e+06  
TotalSalesQuantity        33.000000    261.000000   1929.250000  3.349390e+05  
TotalSalesDollars        729.220000   5298.045000  28396.915000  5.101920e+06  
TotalSalesPrice          289.710000   2857.800000  16059.562500  6.728193e+05  
TotalExciseTax             4.800000     46.570000    418.650000  3.682428e+05  
FreightCost            14069.870000  50293.620000  79528.990000  2.570321e+05  
GrossProfit               52.920000   1399.640000   8660.200000  1.290668e+06  
ProfitMargin              13.324515     30.405457     39.956135  9.971666e+01  
StockTurnover              0.807229      0.981529      1.039342  2.745000e+02  
SalesPurchaseRatio         1.153729      1.436894      1.665449  3.529286e+02

In [5]:
# Select numeric columns only
numeric_cols = df.select_dtypes(include='number').columns.tolist()

# Create 4x4 subplots
fig = make_subplots(
    rows=4, cols=4, 
    subplot_titles=numeric_cols)

# Add histogram for each numeric column
for i, col in enumerate(numeric_cols):
    row = i // 4 + 1
    col_pos = i % 4 + 1
    fig.add_trace(
        go.Histogram(x=df[col], nbinsx=50, name=col),
        row=row, col=col_pos)

# Update layout
fig.update_layout(
    height=1200, width=1200,
    title_text="4x4 Numeric Plot Matrix",
    showlegend=False)

fig.show()

In [6]:
# Outliers detection with Boxplot
# Create 4x4 subplots
fig = make_subplots(
    rows=4, cols=4, 
    subplot_titles=numeric_cols)

# Add box plot for each numeric column
for i, col in enumerate(numeric_cols):
    row = i // 4 + 1
    col_pos = i % 4 + 1
    fig.add_trace(
        go.Box(y=df[col], name=col, boxpoints='outliers'),
        row=row, col=col_pos)

# Update layout
fig.update_layout(
    height=1200, width=1200,
    title_text="4x4 Box Plot Matrix",
    showlegend=False)

fig.show()

## Summary Statistics Insights:

### Negative and Zero Values:
- Gross Profit : Minimumvalue is -52,002.78 , indicating losses. Some products or transections may be sellling at a loss due to high costs or selling at discounts lower than the purchase price.
- Profit Margin : It has a minimun of `-infinity` , which suggests cases where revenue is `Zero` or even lower than costs. 
- Total Sales Quantuty & Dollars : Minimum values are `Zero`, meaning some products were purchased but never sold. These could be clow moving or obsolete stock.

### Outliers indicated by high Standard Deviations :
- `Purchase & Actual Price` : The `max` values (5,681.81 & 7,499.99) are significantly higher than the `mean`(24.39 & 35.64), indicating potential premium product.
- `Freight Cost` : Huge Variation, from 0.09 to 2,57,032.07, suggests logistics inefficiencies or bulk shipments.
- `Stock Turnover` : Ranges from 0 to 274.5, implying some product were sold extremely fast while others remain in stock indefinitely. Value more than 1 sold quantity for that product is higher than purchased quantity due to either sales are being fulfilled from older stock.

In [7]:
# filtering the data by removing inconsistencies
df = pd.read_sql_query("""
SELECT *
FROM vendor_sales_summary
WHERE GrossProfit > 0
AND ProfitMargin > 0
AND TotalSalesQuantity > 0""", conn)
df

VendorNumber                     VendorName  Brand  \
0                2  IRA GOLDMAN AND WILLIAMS, LLP  90085   
1               60        ADAMBA IMPORTS INTL INC    771   
2              105             ALTAMAR BRANDS LLC   2529   
3              105             ALTAMAR BRANDS LLC   8412   
4              200      AMERICAN SPIRITS EXCHANGE  20789   
...            ...                            ...    ...   
8559        172662                SWEETWATER FARM   2191   
8560        172662                SWEETWATER FARM   2265   
8561        172662                SWEETWATER FARM   3632   
8562        173357            TAMWORTH DISTILLING   3909   
8563        201359             FLAVOR ESSENCE INC  90609   

                       Description  PurchasePrice  ActualPrice  Volume  \
0     Ch Lilian 09 Ladouys St Este          23.86        36.99   750.0   
1      Bak's Krupnik Honey Liqueur          11.44        14.99   750.0   
2                        Right Gin          23.25        29.99   750.0   
3        Tequila Ocho Plata Fresno          35.71        49.99   750.0   
4              Zin-phomaniac Znfdl           9.73        14.99   750.0   
...                            ...            ...          ...     ...   
8559  Clark & Chesterfield Whiskey          14.70        19.99   375.0   
8560           Monadnock Moonshine          21.47        28.99   750.0   
8561                Ashuelot Vodka          21.58        28.49   750.0   
8562          White Mountain Vodka          19.37        24.99   750.0   
8563  Flavor Essence Variety 5 Pak          17.00        24.99   162.5   

      TotalPurchaseQuantity  TotalPurchaseDollars  TotalSalesQuantity  \
0                         8                190.88                18.0   
1                        39                446.16                47.0   
2                        12                279.00                12.0   
3                       320              11427.20               307.0   
4                        96                934.08                84.0   
...                     ...                   ...                 ...   
8559                    138               2028.60               125.0   
8560                    267               5732.49               222.0   
8561                    554              11955.32               452.0   
8562                   1232              23863.84               982.0   
8563                      1                 17.00                59.0   

      TotalSalesDollars  TotalSalesPrice  TotalExciseTax  FreightCost  \
0                665.82           295.92            2.00        27.08   
1                704.53           494.67           37.01       367.52   
2                359.88            59.98            9.44        62.39   
3              15346.93         12947.41          242.15        62.39   
4               1511.16           287.84            9.43         6.19   
...                 ...              ...             ...          ...   
8559            2498.75          1819.09           49.00       178.34   
8560            6435.78          5363.15          175.13       178.34   
8561           12877.48          8205.12          356.14       178.34   
8562           24540.18         14469.21          773.87       202.50   
8563            1474.41          1324.47            1.24         0.09   

      GrossProfit  ProfitMargin  StockTurnover  SalesPurchaseRatio  
0          474.94     71.331591       2.250000            3.488160  
1          258.37     36.672675       1.205128            1.579097  
2           80.88     22.474158       1.000000            1.289892  
3         3919.73     25.540808       0.959375            1.343018  
4          577.08     38.187882       0.875000            1.617806  
...           ...           ...            ...                 ...  
8559       470.15     18.815408       0.905797            1.231761  
8560       703.29     10.927813       0.831461            1.122685  
8561       922.16    

In [8]:
# Select numeric columns only
numeric_cols = df.select_dtypes(include='number').columns.tolist()

# Create 4x4 subplots
fig = make_subplots(
    rows=4, cols=4, 
    subplot_titles=numeric_cols)

# Add histogram for each numeric column
for i, col in enumerate(numeric_cols):
    row = i // 4 + 1
    col_pos = i % 4 + 1
    fig.add_trace(
        go.Histogram(x=df[col], nbinsx=50, name=col),
        row=row, col=col_pos)

# Update layout
fig.update_layout(
    height=1200, width=1200,
    title_text="4x4 Numeric Plot Matrix",
    showlegend=False)

fig.show()


In [10]:
df.columns

Index(['VendorNumber', 'VendorName', 'Brand', 'Description', 'PurchasePrice',
       'ActualPrice', 'Volume', 'TotalPurchaseQuantity',
       'TotalPurchaseDollars', 'TotalSalesQuantity', 'TotalSalesDollars',
       'TotalSalesPrice', 'TotalExciseTax', 'FreightCost', 'GrossProfit',
       'ProfitMargin', 'StockTurnover', 'SalesPurchaseRatio'],
      dtype='object')

In [ ]:
# Plotting categorical columns 
category_cols= ['VendorName', 'Description']

# Create subplots
fig = make_subplots(
    rows=1, cols=2, 
    subplot_titles=category_cols)

vendor_counts= df['VendorName'].value_counts().head(10)
desc_counts= df['VendorName'].value_counts().head(10)

# Add VendorName bar chart
fig.add_trace(
    go.Bar(x=vendor_counts.index, y=vendor_counts.values, name="VendorName"),
    row=1, col=1
)

# Add Description bar chart
fig.add_trace(
    go.Bar(x=desc_counts.index, y=desc_counts.values, name="Description"),
    row=1, col=2
)

# bar chart for top 10 VendorName & Description
fig.update_layout(height=800, width=800)


In [69]:
# Correlation Heatmap
corr_matrix = df[numeric_cols].corr()

# plot heatmap
fig= px.imshow(
    corr_matrix,
    text_auto=True,
    color_continuous_scale="RdBu_r",
    title="Correlation Heatmap of Numeric Features"
)

fig.update_layout(height=800, width=800)
fig.show()

## Correlation Insights

- Purchase Price has weak correlation with ToatalSalesDollars & GrossProfit. That indicates price variation do not significantly impact sales revenue or profit.
- Strong correlation between total purchase quantity and total sales quantity(.999), which confirms efficient inventory turnover.
- The other correlations are mentioned bellow. 

## Data Analysis

- Identify Brands that needs promotional or pricing adjustments which exhibits lower sales performance but higher profit mergin.

In [ ]:
brand_performance= df.groupby('Description').agg({
    'TotalSalesDollars': 'sum',
    'ProfitMargin' : 'mean'
}).reset_index()

In [39]:
low_sales_threshold= brand_performance['TotalSalesDollars'].quantile(0.15)
high_profit_threshold= brand_performance['ProfitMargin'].quantile(0.85)

In [ ]:
# Filtering brands with low sales but high profit margin
target_brands = brand_performance[
    (brand_performance['TotalSalesDollars'] <= low_sales_threshold) &
    (brand_performance['ProfitMargin'] >= high_profit_threshold)
]
print('Brands with Low sales but High profit Margins:')
display(target_brands.sort_values('TotalSalesDollars'))

Brands with Low sales but High profit Margins:


Description  TotalSalesDollars  ProfitMargin
6199    Santa Rita Organic Svgn Bl               9.99     66.466466
2369             Debauchery Pnt Nr              11.58     65.975820
2070   Concannon Glen Ellen Wh Zin              15.95     83.448276
2188             Crown Royal Apple              27.86     89.806174
6237  Sauza Sprklg Wild Berry Marg              27.96     82.153076
...                            ...                ...           ...
5074   Nanbu Bijin Southern Beauty             535.68     76.747312
2271         Dad's Hat Rye Whiskey             538.89     81.851584
57       A Bichot Clos Marechaudes             539.94     67.740860
6245     Sbragia Home Ranch Merlot             549.75     66.444748
3326     Goulee Cos d'Estournel 10             558.87     69.434752

[198 rows x 3 columns]

In [53]:
fig = px.scatter(
    target_brands,
    x="TotalSalesDollars",
    y="ProfitMargin",
    size="TotalSalesDollars",
    color="ProfitMargin",
    hover_data=["Description"],   # show labels directly
    title="Target Brands: Profit Margin vs Total Sales"
)

# Add threshold lines
fig.add_vline(x=low_sales_threshold, line_dash="dash", line_color="red",
              annotation_text="Sales Threshold", annotation_position="top left")

fig.add_hline(y=high_profit_threshold, line_dash="dash", line_color="blue",
              annotation_text="Profit Threshold", annotation_position="bottom right")

fig.update_layout(height= 600, width= 1200)

Which vendors and brands demonstrates the highest sales performance

In [61]:
def format_dollar(value):
    if value >= 1000000:
        return f'{value / 1000000:.2f}M'
    elif value >= 1000:
        return f'{value/1000:.2f}K'
    else:
        return str(value)

In [67]:
# Top vendors and brands by Performance
top_vendors= df.groupby('VendorName')['TotalSalesDollars'].sum().nlargest(10)
top_brands= df.groupby('Description')['TotalSalesDollars'].sum().nlargest(10)
top_vendors= top_vendors.apply(lambda x : format_dollar(x))
top_vendors

VendorName
DIAGEO NORTH AMERICA INC      67.99M
MARTIGNETTI COMPANIES         39.33M
PERNOD RICARD USA             32.06M
JIM BEAM BRANDS COMPANY       31.42M
BACARDI USA INC               24.85M
CONSTELLATION BRANDS INC      24.22M
E & J GALLO WINERY            18.40M
BROWN-FORMAN CORP             18.25M
ULTRA BEVERAGE COMPANY LLP    16.50M
M S WALKER INC                14.71M
Name: TotalSalesDollars, dtype: object

In [65]:
top_brands= top_brands.apply(lambda x : format_dollar(x))
top_brands

Description
Jack Daniels No 7 Black    7.96M
Tito's Handmade Vodka      7.40M
Grey Goose Vodka           7.21M
Capt Morgan Spiced Rum     6.36M
Absolut 80 Proof           6.24M
Jameson Irish Whiskey      5.72M
Ketel One Vodka            5.07M
Baileys Irish Cream        4.15M
Kahlua                     3.60M
Tanqueray                  3.46M
Name: TotalSalesDollars, dtype: object

In [78]:
# Visualizing top 10 vendors and brands
# Create subplots
fig = make_subplots(
    rows=1, cols=2, )

# Add VendorName bar chart
fig.add_trace(
    go.Bar(x=top_vendors.index, y=top_vendors.values, name="VendorName"),
    row=1, col=1
)

# Add VendorName bar chart
fig.add_trace(
    go.Bar(x=top_brands.index, y=top_brands.values, name="VendorName"),
    row=1, col=2
)

fig.show()